In [15]:
%%writefile bonus_synthetic_biofilm.py

Overwriting bonus_synthetic_biofilm.py


In [16]:
!python bonus_synthetic_biofilm.py

In [17]:
"""
Bonus Challenge — Synthetic 3D Biofilm (Option A)

  1) Synthesizes 3D "biofilm-like" TIFF volume
  2) Segments it (Gaussian + Otsu + largest connected component)
  3) Computes metrics: biovolume (µm³), mean intensity, surface area (µm²),
     mean/max local thickness (µm) via EDT
  4) Saves:
       - outputs/metrics.csv, outputs/metrics.json
       - outputs/synthetic_biofilm.tif  (raw volume)
       - outputs/segmentation_mask.tif
       - outputs/local_thickness_um.tif
       - outputs/mesh_thickness.html    (interactive 3D surface, color = thickness)

Felipe Garcia Cruz
"""

import os, json
import numpy as np
import pandas as pd
import tifffile as tiff
from scipy.ndimage import gaussian_filter, distance_transform_edt, label
from skimage.measure import marching_cubes
import plotly.graph_objects as go


# Synthetic data

def make_synthetic_biofilm(Z=80, Y=256, X=256, seed=42):
    rng = np.random.default_rng(seed)
    zz, yy, xx = np.meshgrid(
        np.linspace(-1, 1, Z), np.linspace(-1, 1, Y), np.linspace(-1, 1, X), indexing="ij"
    )

    # Core (ellipsoid) + a few Gaussian filaments
    r = np.sqrt((zz/0.7)**2 + (yy/0.9)**2 + (xx/0.9)**2)
    core = (r < 1.0).astype(float)

    fil1 = np.exp(-((yy-0.30)**2 + (xx+0.20)**2)/(2*0.03**2)) * np.exp(-((zz+0.20)**2)/(2*0.12**2))
    fil2 = np.exp(-((yy+0.25)**2 + (xx-0.25)**2)/(2*0.03**2)) * np.exp(-((zz-0.15)**2)/(2*0.10**2))
    fil3 = np.exp(-((yy-0.35)**2 + (xx-0.35)**2)/(2*0.02**2)) * np.exp(-((zz+0.25)**2)/(2*0.08**2))

    vol_f = (core + 2.2*(fil1+fil2) + 2.8*fil3)
    vol_f = vol_f / vol_f.max()

    # Add noise and scale to ~12-bit
    vol = (vol_f * 3500 + rng.normal(0, 120, size=vol_f.shape)).clip(0, 4095).astype(np.uint16)
    return vol


# Utilities

def otsu_threshold(arr, nbins=256):
    a = arr.astype(np.float32)
    a_min, a_max = float(a.min()), float(a.max())
    if a_min == a_max:
        return a_min
    hist, bin_edges = np.histogram(a, bins=nbins, range=(a_min, a_max))
    bin_centers = (bin_edges[:-1] + bin_edges[1:]) / 2.0

    weight1 = np.cumsum(hist)
    weight2 = np.cumsum(hist[::-1])[::-1]
    # avoid divide-by-zero by clamping
    mean1 = np.cumsum(hist * bin_centers) / np.maximum(weight1, 1e-12)
    mean2 = (np.cumsum((hist * bin_centers)[::-1]) / np.maximum(weight2[::-1], 1e-12))[::-1]
    between = weight1[:-1] * weight2[1:] * (mean1[:-1] - mean2[1:])**2
    idx = int(np.argmax(between))
    return float(bin_centers[idx])

def remove_small_objects(mask, min_size=500):
    lab, n = label(mask)
    if n == 0:
        return mask
    counts = np.bincount(lab.ravel())
    keep = np.where(counts >= min_size)[0]
    keep = keep[keep != 0]  # never keep background
    return np.isin(lab, keep)

def keep_largest_cc(mask):
    lab, n = label(mask)
    if n == 0:
        return mask
    counts = np.bincount(lab.ravel())
    counts[0] = 0  # ignore background
    largest = int(np.argmax(counts))
    return lab == largest

def surface_area_from_mesh(verts, faces):
    v0 = verts[faces[:, 0]]
    v1 = verts[faces[:, 1]]
    v2 = verts[faces[:, 2]]
    cross = np.cross(v1 - v0, v2 - v0)
    areas = 0.5 * np.linalg.norm(cross, axis=1)
    return float(areas.sum())

def sample_thickness_at_vertices(verts, thickness_map, spacing):
    dz, dy, dx = spacing
    nz, ny, nx = thickness_map.shape
    iz = np.clip(np.round(verts[:, 0] / dz).astype(int), 0, nz-1)
    iy = np.clip(np.round(verts[:, 1] / dy).astype(int), 0, ny-1)
    ix = np.clip(np.round(verts[:, 2] / dx).astype(int), 0, nx-1)
    return thickness_map[iz, iy, ix]

def save_plotly_mesh(verts, faces, colors, out_html, title="Surface colored by local thickness (µm)"):
    mesh = go.Mesh3d(
        x=verts[:, 2], y=verts[:, 1], z=verts[:, 0],   # (x,y,z) from (z,y,x)
        i=faces[:, 0], j=faces[:, 1], k=faces[:, 2],
        intensity=colors, colorscale="Viridis", showscale=True,
        flatshading=False, lighting=dict(ambient=0.5, diffuse=0.7, specular=0.2),
        colorbar=dict(title="Thickness (µm)")
    )
    fig = go.Figure(data=[mesh])
    fig.update_layout(
        title=title, scene_aspectmode="data",
        scene=dict(xaxis_title="X (µm)", yaxis_title="Y (µm)", zaxis_title="Z (µm)")
    )
    fig.write_html(out_html, include_plotlyjs="cdn")


# Main pipeline

def run_pipeline_on_synthetic(outdir="outputs",
                              voxel_size_um=(0.3, 0.108, 0.108),
                              sigma=1.0,
                              min_size=500):
    """
    Create synthetic stack and run the analysis/visualization pipeline.
    """
    os.makedirs(outdir, exist_ok=True)

    # 1) Synthesize and save raw volume
    vol = make_synthetic_biofilm()
    raw_path = os.path.join(outdir, "synthetic_biofilm.tif")
    tiff.imwrite(raw_path, vol, photometric="minisblack")

    dz, dy, dx = voxel_size_um

    # 2) Smooth + Otsu threshold
    v_sm = gaussian_filter(vol.astype(np.float32), sigma=sigma) if sigma > 0 else vol.astype(np.float32)
    thr = otsu_threshold(v_sm)
    mask = v_sm > thr

    # 3) Clean-up: remove tiny bits + keep largest component
    if min_size and min_size > 0:
        mask = remove_small_objects(mask, min_size=min_size)
    mask = keep_largest_cc(mask)

    # 4) Local thickness: 2 * EDT (in µm because of sampling)
    dist_um = distance_transform_edt(mask, sampling=(dz, dy, dx))
    thickness_um = (2.0 * dist_um).astype(np.float32)
    thickness_um[~mask] = 0.0

    # 5) Surface mesh via marching cubes (spacing gives physical units)
    verts, faces, _, _ = marching_cubes(mask.astype(np.float32), level=0.5, spacing=(dz, dy, dx))
    v_thick = sample_thickness_at_vertices(verts, thickness_um, (dz, dy, dx))

    # 6) Metrics
    voxel_vol_um3 = dz * dy * dx
    biovolume_um3 = float(mask.sum()) * voxel_vol_um3
    intensity_mean = float(vol[mask].mean()) if mask.any() else float("nan")
    thickness_mean = float(thickness_um[mask].mean()) if mask.any() else 0.0
    thickness_max  = float(thickness_um.max()) if mask.any() else 0.0
    surface_area_um2 = surface_area_from_mesh(verts, faces)

    metrics = {
        "input": "synthetic_biofilm (generated)",
        "voxel_size_um": {"dz": dz, "dy": dy, "dx": dx},
        "biovolume_um3": biovolume_um3,
        "mean_intensity": intensity_mean,
        "surface_area_um2": surface_area_um2,
        "thickness_mean_um": thickness_mean,
        "thickness_max_um": thickness_max,
        "num_voxels": int(mask.sum())
    }

    # 7) Save all outputs
    tiff.imwrite(os.path.join(outdir, "segmentation_mask.tif"), mask.astype(np.uint8))
    tiff.imwrite(os.path.join(outdir, "local_thickness_um.tif"), thickness_um)
    save_plotly_mesh(verts, faces, v_thick, os.path.join(outdir, "mesh_thickness.html"))
    pd.DataFrame([metrics]).to_csv(os.path.join(outdir, "metrics.csv"), index=False)
    with open(os.path.join(outdir, "metrics.json"), "w") as f:
        json.dump(metrics, f, indent=2)

    # Console summary
    print("Done. Metrics:")
    for k, v in metrics.items():
        if k != "voxel_size_um":
            print(f"  {k}: {v}")
    print(f"\nOutputs written to: {os.path.abspath(outdir)}")


if __name__ == "__main__":
    run_pipeline_on_synthetic(
        outdir="outputs",
        voxel_size_um=(0.3, 0.108, 0.108),  # dz, dy, dx in µm (pick plausible values)
        sigma=1.0,
        min_size=500
    )


Done. Metrics:
  input: synthetic_biofilm (generated)
  biovolume_um3: 5336.7978815999995
  mean_intensity: 930.0938885931071
  surface_area_um2: 1794.468456609997
  thickness_mean_um: 5.152728080749512
  thickness_max_um: 16.383283615112305
  num_voxels: 1525148

Outputs written to: /content/outputs


In [18]:
import os, pandas as pd
from IPython.display import HTML

outdir = "/content/outputs"

# Metrics table
display(pd.read_csv(os.path.join(outdir, "metrics.csv")))

# Interactive surface (color = local thickness, in µm)
HTML(open(os.path.join(outdir, "mesh_thickness.html")).read())


input                          voxel_size_um  \
0  synthetic_biofilm (generated)  {'dz': 0.3, 'dy': 0.108, 'dx': 0.108}   

   biovolume_um3  mean_intensity  surface_area_um2  thickness_mean_um  \
0    5336.797882      930.093889       1794.468457           5.152728   

   thickness_max_um  num_voxels  
0         16.383284     1525148

In [19]:
from google.colab import files
!zip -qr /content/outputs.zip /content/outputs
files.download("/content/outputs.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>